### Here we assign workplaces to people 
In each polygon we know the number of people. So we generate workplaces there. 

In [1]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
from shapely.geometry import Point
from tqdm import tqdm
from geopy.distance import great_circle
import random

In [2]:
# SOME AUXILIARY FUNCTIONS
def isSchoolAge(row):
    return row['age'] >= 7 and row['age'] <= 17


def isWorkingAge(row):
    return row['age'] >= 18 and (row['sex'] == 'F' and row['age'] <= 60 or row['sex'] == 'M' and row['age'] <= 55)


def rowPointLocation(row):
    return Point(float(row['latitude']), float(row['longitude']))


def findDistToObj(row, point):
    # finds distances from the selected point to the object represented by DataFrame row
    obj_point = rowPointLocation(row)
    dist = great_circle((point.x, point.y), (obj_point.x, obj_point.y)).km
    return dist

In [3]:
city_name = 'spb'

input_dir_workplaces = '../data/' + city_name + '/workplaces_' + city_name + '_2023.txt'
input_dir_people = '../data/' + city_name + '/people_' + city_name + '_2023_splitted_dwellings.txt'
input_dir_households = '../data/' + city_name + '/households_' + city_name + '_2023_splitted_dwellings.txt'
output_dir = '../data/' + city_name + '/people_' + city_name + '_2023_assigned_workplaces.txt'


people_df = pd.read_csv(input_dir_people, sep='\t')
households_df = pd.read_csv(input_dir_households, sep='\t')
workplaces_df = pd.read_csv(input_dir_workplaces, sep='\t')



hh_points_dic = {}

list_keys = households_df['sp_id'].tolist()
list_values = [Point([row['latitude'], row['longitude']])
               for idx, row in tqdm(households_df.iterrows())]

for key, value in zip(list_keys, list_values):
    hh_points_dic[key] = value

5294136it [04:00, 22022.14it/s]


In [4]:
def assignWorkplaces(df_orig, hh_points_dic, workplaces_df_orig) -> pd.DataFrame:

    print("Assigning workplaces started...")
    assign_type = '15km' # 'closest' or any ohter string to apply less than 15km radius workplace
    print("CLOSEST WORKPLACE" if assign_type == 'closest' else "IN DISTANCE <= 15km")
    df = df_orig[df_orig.apply(isWorkingAge, axis=1)]
    
    print('Removed people without work...')
    
    close_work_ids = []
    workers_num = {}
    
    print("Workplaces, total: {}".format(workplaces_df_orig['size'].sum()))
    print("Working people, total: {}".format(df.shape[0]))

    df_add = pd.DataFrame(list(np.zeros(workplaces_df_orig.shape[0])), columns=[
                          'distances'], index=workplaces_df_orig.index)
    
    workplaces_df = workplaces_df_orig.join(df_add)
    print(workplaces_df)
    allWorkplacesFilled = False
    
    print(df.shape)
    for idx in tqdm(range(int(df.shape[0]))):
    # for idx in tqdm(range(100)):
        person_row = df.iloc[idx]
        person_point = hh_points_dic[person_row['sp_hh_id']]
        
        series_distance = workplaces_df.apply(
            findDistToObj, args=(person_point,), axis=1)
        # print(series_distance)
        df_add = pd.DataFrame(series_distance.tolist(), columns=[
                              'distances'], index=workplaces_df.index)
        
        workplaces_df.update(df_add)
        isWorkerAssigned = False
        
        while not isWorkerAssigned:
            # print("Schools: \n", schools_df)
            # print("Work distances: \n", workplaces_df['distances'])
            
            close_workplace = None
            min_index = 0
            ### ASSIGN CLOSEST WORKPLACE
            if (assign_type == 'closest'):
                min_index = workplaces_df['distances'].idxmin()
                close_workplace = workplaces_df.loc[min_index]
                print(close_workplace)
            ### ASSIGN FROM SOME DISTANCE    
            else: 
                workplaceCloseEnough = False 
                counter = 0
                while (not workplaceCloseEnough):
                    random.seed(10)
                    min_index = np.random.choice(workplaces_df['distances'].index, size=1)[0]
                    close_workplace = workplaces_df.loc[min_index]
                    # print(close_workplace['distances'])
                    # print(close_workplace.shape)
                    # print(close_workplace['distances'])
                    counter+=1
                    if counter >= 100:
                        workplaceCloseEnough = True
                        print('Too much tries to choose working place')
                    if (close_workplace['distances'] <= 15): 
                        # print(close_workplace)
                        workplaceCloseEnough = True
            
            ### ASSIGN             
            if not (close_workplace['sp_id'] in workers_num.keys()):  # checking capacity
                workers_num[close_workplace['sp_id']] = 1
            else:
                workers_num[close_workplace['sp_id']
                             ] = workers_num[close_workplace['sp_id']] + 1
                
            if workers_num[close_workplace['sp_id']] == close_workplace['size']:
                # print("Before: {}".format(schools_df.shape[0]))
                # (schools_df.index[min_index])
                # print(min_index)
                
                workplaces_df = workplaces_df.drop(min_index, errors='ignore')
                # print("After: {}".format(schools_df.shape[0]))

                if workplaces_df.shape[0] == 0:
                    allWorkplacesFilled = True
                    
            isWorkerAssigned = True
        
        close_work_ids.append(close_workplace['sp_id'])

        if allWorkplacesFilled:
            print("All workplaces filled to capacity!")
            break
            
        
    df_orig.update(pd.DataFrame(close_work_ids, columns=[
                   'work_id'], index=df.index[:len(close_work_ids)]))    
    df_orig.to_csv(output_dir, sep='\t')
    return df_orig


import time

start = time.time()
df_assigned = assignWorkplaces(people_df, hh_points_dic, workplaces_df)
end = time.time()
print("Time of execution: {} min".format((end - start)/60))

Assigning workplaces started...
IN DISTANCE <= 15km
Removed people without work...
Workplaces, total: 3350196.0
Working people, total: 3066015
     sp_id   latitude  longitude    size  distances
0      1.0  60.255976  29.570306   311.0        0.0
1      2.0  60.255976  29.606243   757.0        0.0
2      3.0  60.199311  29.660149   264.0        0.0
3      4.0  59.919714  29.696086   561.0        0.0
4      5.0  59.930112  29.696086   583.0        0.0
..     ...        ...        ...     ...        ...
759  760.0  59.862469  30.971857   708.0        0.0
760  761.0  59.867677  30.989825   286.0        0.0
761  762.0  59.878091  30.989825  3252.0        0.0
762  763.0  59.888502  30.989825  1507.0        0.0
763  764.0  59.883297  31.007794   504.0        0.0

[764 rows x 5 columns]
(3066015, 8)


  0%|          | 1701/3066015 [01:09<34:15:36, 24.85it/s]

Too much tries to choose working place


  0%|          | 4866/3066015 [03:18<36:31:29, 23.28it/s]

Too much tries to choose working place


...

Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place


100%|█████████▉| 3066005/3066015 [16:27:33<00:00, 84.99it/s]

Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place
Too much tries to choose working place


100%|██████████| 3066015/3066015 [16:27:33<00:00, 51.74it/s]


Too much tries to choose working place
Time of execution: 988.3776741186778 min


In [6]:
min_idx = workplaces_df['size'].idxmin()
workplaces_df.loc[min_idx]
chosen_idx = np.random.choice(workplaces_df.index, size=1)
workplaces_df = workplaces_df.drop(chosen_idx)
np.random.choice(workplaces_df.index, size=1)[0]

303

In [15]:
df_assigned['work_id'].unique()

array([507.0, 542.0, 440.0, 86.0, 505.0, 370.0, 'X', 85.0, 662.0, 696.0,
       665.0, 509.0, 645.0, 510.0, 76.0, 544.0, 406.0, 74.0, 405.0, 508.0,
       474.0, 439.0, 77.0, 371.0, 601.0, 625.0, 646.0, 661.0, 280.0,
       476.0, 663.0, 504.0, 472.0, 224.0, 470.0, 540.0, 473.0, 506.0,
       539.0, 543.0, 471.0, 475.0, 407.0, 575.0, 664.0, 310.0, 373.0,
       84.0, 576.0, 438.0, 372.0, 135.0, 78.0, 340.0, 151.0, 83.0, 574.0,
       89.0, 541.0, 309.0, 578.0, 441.0, 577.0, 673.0, 477.0, 695.0,
       545.0, 579.0, 688.0, 672.0, 697.0, 511.0, 689.0, 706.0, 705.0,
       686.0, 602.0, 478.0, 687.0, 671.0, 546.0, 674.0, 690.0, 707.0,
       666.0, 512.0, 708.0, 699.0, 710.0, 720.0, 719.0, 718.0, 675.0,
       311.0, 721.0, 667.0, 700.0, 709.0, 676.0, 698.0, 547.0, 103.0,
       122.0, 75.0, 225.0, 79.0, 152.0, 301.0, 112.0, 136.0, 281.0, 408.0,
       123.0, 691.0, 197.0, 253.0, 677.0, 513.0, 442.0, 374.0, 90.0,
       312.0, 104.0, 58.0, 113.0, 243.0, 237.0, 96.0, 199.0, 40.0, 360.0,
  

In [ ]:
# just some tests
# for i in range(100):
#     person_row = df_assigned.iloc[i]
#     hh_id = person_row['sp_hh_id']
#     work_id = person_row['work_id']
#     if person_row['work_id'] != 'X':
#         work = Point(workplaces_df[workplaces_df['sp_id'] == work_id].latitude, workplaces_df[workplaces_df['sp_id'] == work_id].longitude)  
#         hh =  Point(households_df[households_df['sp_id'] == hh_id].iloc[0].latitude, households_df[households_df['sp_id'] == hh_id].iloc[0].longitude) 
#         dist = great_circle((work.x, work.y), (hh.x, hh.y)).km
#         if (dist > 20):
#             print(person_row, dist)
